In [1]:
import json
from pathlib import Path

import numpy as np
import pyslim
import tskit

In [2]:
TREE_FILE = Path("./simplification_test.trees")
PARAM_FILE = Path("simplification_test_params.json")
SEED = 23

In [3]:
MODEL_PARAMS = {
    "K": 5,
    "SD": 0.2,
    "SI": 0.2,
    "SM": 0.2,
    "L": 2,
    "W": 10.0,
    "G": 1e4,
    "MU": 0,
    "R": 1e-8,
    "SIM_END": 2e6,
    "IND_RECORD_LIM": 20,
    "IND_RECORD_LAG": 10,
    "IND_RECORD_FREQ": 200,
    "OUTPATH": str(TREE_FILE),
}

In [4]:
with open(PARAM_FILE, "w") as fp:
    json.dump(MODEL_PARAMS, fp)

In [5]:
!slim -s {SEED} -d PARAM_FILE="'{PARAM_FILE}'" ~/repo/tskit-ld/spatial-ld/sim/slim/main-spatial.slim

// Initial random seed:
23

// RunInitializeCallbacks():
LOG: 06-06-2024_01:47:29 Simulation Start
LOG: 06-06-2024_01:47:29 Working directory /home/lkirk/repo/tskit-ld/spatial-ld/analysis/spatial-positions
LOG: 06-06-2024_01:47:29 Parameters {
	"G" = 10000
	"IND_RECORD_FREQ" = 200
	"IND_RECORD_LAG" = 10
	"IND_RECORD_LIM" = 20
	"K" = 5
	"L" = 2
	"MU" = 0
	"OUTPATH" = "simplification_test.trees"
	"R" = 1.0e-08
	"SD" = 0.2
	"SEED" = 23
	"SI" = 0.2
	"SIM_END" = 2000000
	"SM" = 0.2
	"W" = 10.0
}
initializeSLiMModelType(modelType = 'nonWF');
initializeSLiMOptions(dimensionality = 'xy');
initializeTreeSeq(checkCoalescence = T);
initializeMutationRate(0);
initializeMutationType(1, 0.5, "f", 0);
initializeGenomicElementType(1, m1, 1);
initializeGenomicElement(g1, 0, 9999);
initializeRecombinationRate(1e-08);
initializeInteractionType(1, "xy", reciprocal=T, maxDistance=0.6);
initializeInteractionType(2, "xy", reciprocal=T, maxDistance=0.6);

// Starting run at tick <start>:
1 

LOG: 06-06-2024_0

In [13]:
ts = tskit.load(TREE_FILE)

In [29]:
if all_coalesced := (np.array([t.num_roots for t in ts.trees()]) == 1).all():                                                                              
    print("all trees have coalesced")

all trees have coalesced


In [14]:
ts.max_root_time

79541.0

Just taking a uniform sample of individuals alive at various time points

In [15]:
alive_before_simplification = []
for t in range(0, int(ts.max_root_time), 1000):
    alive_before_simplification.append(pyslim.individuals_alive_at(ts, t))

Now, looking at individuals alive at our various sampling points

In [16]:
alive_at_sampling_points = []
for t in ts.metadata['SLiM']['user_metadata']['sampling_times']:
    alive_at_sampling_points.append(pyslim.individuals_alive_at(ts, t))

Odd...

In [17]:
alive_at_sampling_points

[array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64),
 array([], dtype=int64)]

In [25]:
keep = [s for a in alive_before_simplification for s in a]

In [26]:
len(keep)

3883

In [27]:
ts

In [28]:
for i in keep:
    try:
        keep.extend(ts.individual(i).nodes)
    except:
        print(i, 'is not an individual?')

36256 is not an individual?
36257 is not an individual?
36258 is not an individual?
36259 is not an individual?
36260 is not an individual?
36261 is not an individual?
36262 is not an individual?
36263 is not an individual?
36264 is not an individual?
36265 is not an individual?
36266 is not an individual?
36267 is not an individual?
36268 is not an individual?
36269 is not an individual?
36270 is not an individual?
36271 is not an individual?
36272 is not an individual?
36273 is not an individual?
36274 is not an individual?
36275 is not an individual?
36276 is not an individual?
36277 is not an individual?
36278 is not an individual?
36279 is not an individual?
36280 is not an individual?
36281 is not an individual?
36282 is not an individual?
36283 is not an individual?
36284 is not an individual?
36285 is not an individual?
36286 is not an individual?
36287 is not an individual?
36288 is not an individual?
36289 is not an individual?
36290 is not an individual?
36291 is not an indi

In [33]:
ts.samples()

array([    0,     1,     2, ..., 38373, 38374, 38375], dtype=int32)

In [30]:
roots = [t.root for t in ts.trees()]

In [31]:
roots

[57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707,
 57707]

In [35]:
keep = list(set(keep))

In [36]:
sts = ts.simplify(samples=keep, keep_input_roots=True)

In [37]:
sts

In [38]:
ts

In [39]:
alive_after_simplification = []
for t in range(0, int(sts.max_root_time), 1000):
    alive_after_simplification.append(pyslim.individuals_alive_at(sts, t))

In [42]:
for before, after in zip(alive_before_simplification, alive_after_simplification):
    assert((before == after).all())

AssertionError: 

In [55]:
for before, after in zip(alive_before_simplification, alive_after_simplification):
    assert((len(before) == len(after)))

In [43]:
before

array([14272, 14273, 14274, ..., 15297, 15298, 15299])

In [44]:
after

array([8130, 8131, 8132, ..., 9155, 9156, 9157])

In [46]:
len(set([s for a in alive_before_simplification for s in a]) ^ set([s for a in alive_after_simplification for s in a]))

5446

In [48]:
len([s for a in alive_before_simplification for s in a])

3883

In [49]:
len([s for a in alive_after_simplification for s in a])

3883

In [51]:
len(set([s for a in alive_before_simplification for s in a]) ^ set(sts.samples()))

19870

In [59]:
(ts.individuals_location[alive_before_simplification[4], :] == sts.individuals_location[alive_after_simplification[4], :]).all()

True

In [60]:
for before, after in zip(alive_before_simplification, alive_after_simplification):
    assert((ts.individuals_location[before, :] == sts.individuals_location[after, :]).all())